# Testing possible algorithms to solve MDHVRPTW

Travelling salesman problem

TSP es *casi* MDHVRPTW (*Multi-Depot Heterogeneous VRP with Time Windows) *del profe* pero:
- Solo 1 camion
- Todos los ciudades (aka. almacenes pequeños) tienen al menos 1 pedido
- Capacidad infinita (1 solo tipo de vehiculo)
- Sin ventanas de tiempo (aka. plazos de entrega)
- Solo 1 deposito
- No hay entregas parciales
  - Relajar la restriccion de que la demanda de los "customers" debe ser satisfecha al 100% por
    un solo camion.  Entonces, si un "customer" requiere 8 paquetes,  se le puede entregar solo 5,
    y quedan pendientes 3.  **Esto modifica la solucion,  ahora es una lista donde los nodos a visitar
    ya no son unicos**.  Se debe terminar la solucion cuando ya no hayan pedidos pendientes (paquetes por entregar > 0).
- No hay "trasvaces"
  - F

Cambios identificados, necesarios para adaptar el TSP a nuestro caso:
- Tramos no conectados -> distancia grande entre ellos
- Distancias no son euclidianas, usar "geodistance"
- [...]

## Posibilidades

Una manera de implementar 

- [scikit-opt](https://github.com/guofei9987/scikit-opt)

## NetworkX to find all_pairs_shortest_path

In [ ]:
import networkx as nx
G = nx.Graph()
G.add_edge(1, 2)  # default edge data=1
G.add_edge(2, 3, weight=0.9)  # specify edge data

In [ ]:
import math
G.add_edge('y', 'x', function=math.cos)
G.add_node(math.cos)  # any hashable can be a node

In [ ]:
elist = [(1, 2), (2, 3), (1, 4), (4, 2)]
G.add_edges_from(elist)
elist = [('a', 'b', 5.0), ('b', 'c', 3.0), ('a', 'c', 1.0), ('c', 'd', 7.3)]
G.add_weighted_edges_from(elist)

In [ ]:
import matplotlib.pyplot as plt
#G = nx.cubical_graph()
subax1 = plt.subplot(121)
nx.draw(G)   # default spring_layout

In [ ]:
print(G.adj)

## Pre-processing

La data del profe es muy tedioso de leer.  Formato raro.  Pasar primero a csv.

Distancia entre nodos:

In [8]:
%pwd

'/home/mitsuo/docs/courses/2022-1/INF226_DP1/project/code/DP_project/test'

In [1]:
import numpy as np

import csv
import math
import random

import networkx as nx
import matplotlib.pyplot as plt

In [2]:
def degreesToRadians(degrees):
    return degrees * math.pi / 180

def distanceInKmBetweenEarthCoordinates(lat1, lon1, lat2, lon2):
    earthRadiusKm = 6371        # Avg. radius

    dLat = degreesToRadians(lat2-lat1)
    dLon = degreesToRadians(lon2-lon1)

    lat1 = degreesToRadians(lat1)
    lat2 = degreesToRadians(lat2)

    a = math.sin(dLat/2) * math.sin(dLat/2) \
      + math.sin(dLon/2) * math.sin(dLon/2) * math.cos(lat1) * math.cos(lat2)
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1-a));
    return earthRadiusKm * c


In [3]:
class Node:
    """
    
    Attributes
    ----------
    lat : float
        Latitud (angulo de los Paralelos) en grados sexagesimales
    lon : float
        Longitud (angulo de los Meridianos) en grados sexagesimales
    x : float
        Aproximacion local, en Km respecto ("Lima": -12.04591952,-77.03049615  (lat, long))
        x = (longitud - (-77.03049615)) * (pi / 180) * earthRadiusKm
    y : float
        Aproximacion local, en Km respecto ("Lima")
        y = (latitud - (-12.04591952)) * (pi / 180) * earthRadiusKm
    demand : float
        Cantidad de paquetes  (facil cambiar a int)
    *_time : float
        Cantidades de tiempo en minutos
    
    Notes
    -----
    Web Mercator projection (BAD):
    
        x = floor(256 / (2 * math.pi) * 2**(zoom_level) * (lon + math.pi))
        y = floor(265 / (2 * math.pi) * 2**(zoom_level) * (math.pi - math.ln(math.tan( math.pi / 4 + lat / 2 ))))
        
        x = R * lon
        y = R * ln(tan(pi/4 + lat/2)
    
    Both `lon` and `lat` in radians.
    
    "Lima": -12.04591952,-77.03049615  (lat, long)
    """
    def __init__(self, id:  int, ubigeo, lat, lon, is_depot,
                 demand, ready_time, due_time, service_time):
        super()
        self.id = id
        self.ubigeo = ubigeo

        if is_depot:
            self.is_depot = True
        else:
            self.is_depot = False
    
        earthRadiusKm = 6371        # Avg. radius
        zoom_level = 1
        lima_lat = (-12.04591952)
        lima_lon = (-77.03049615)
        
        self.lat = lat
        self.lon = lon
        self.x = (lon - lima_lon) * (math.pi / 180) * earthRadiusKm
        self.y = (lat - lima_lat) * (math.pi / 180) * earthRadiusKm
        #self.lat *= (math.pi / 180)
        #self.lon *= (math.pi / 180)
        #self.x = 256 / (2 * math.pi) * 2**(zoom_level) * (self.lon + math.pi)
        #self.y = 256 / (2 * math.pi) * 2**(zoom_level) * (math.pi - math.log(math.tan( math.pi / 4 + self.lat / 2 )))
        self.x = round(self.x, 3)
        self.y = round(self.y, 3)
        self.demand = demand
        self.ready_time = 0 #ready_time
        self.due_time = due_time
        self.service_time = service_time

In [10]:
nodes = []

with open('data/VRPTW_python/inf226.oficinas_mod.csv', newline='') as csvfile:
    orders = csv.reader(csvfile)
    count = 1
    id = 0
    for row in orders:
        if count >= 2:
            ubigeo, dept, prov, latitud, longitud, region_natural, is_depot = row[:7]
            demand, ready_time, due_time, service_time = row[7:]
            nodes.append(Node(
                id, ubigeo, float(latitud), float(longitud), int(is_depot),
                #int(100 * random.random()), 0, int(5000 + 500 * (1.5 - random.random())), service_time=60
                demand=float(demand), ready_time=0, due_time=float(due_time), service_time=60
            ))
            id += 1
        count += 1

In [12]:
for node in nodes:
    if node.is_depot:
        print(node.__dict__)

{'id': 34, 'ubigeo': '040101', 'is_depot': True, 'lat': -16.39881421, 'lon': -71.537019649, 'x': 610.847, 'y': -484.02, 'demand': 0.0, 'ready_time': 0, 'due_time': 8000.0, 'service_time': 60}
{'id': 122, 'ubigeo': '130101', 'is_depot': True, 'lat': -8.11176389, 'lon': -79.02868652, 'x': -222.189, 'y': 437.458, 'demand': 0.0, 'ready_time': 0, 'due_time': 8000.0, 'service_time': 60}
{'id': 134, 'ubigeo': '150101', 'is_depot': True, 'lat': -12.04591952, 'lon': -77.03049615, 'x': 0.0, 'y': 0.0, 'demand': 0.0, 'ready_time': 0, 'due_time': 8000.0, 'service_time': 60}


In [15]:
node_num = len(nodes)

tramos = []
with open('../data/inf226.tramos.v.2.0.csv', newline='') as f:
    rows = csv.reader(f)
    count = 1
    for row in rows:
        if count >= 2:
            tramos.append([row[0], row[1]])
        count += 1

In [16]:
print(len(tramos))
tramos[:5]

7008


[['010201', '010301'],
 ['010301', '010201'],
 ['010201', '010401'],
 ['010401', '010201'],
 ['010201', '010501']]

In [17]:
node_dist_mat = np.zeros((node_num, node_num))

nodes_d = dict(zip([n.ubigeo for n in nodes], nodes))
for ubigeo1, ubigeo2 in tramos:
    #if ubigeo1 in nodes_d.keys() and ubigeo2 in nodes_d.keys():
    id1 = nodes_d[ubigeo1].id
    id2 = nodes_d[ubigeo2].id
    n1 = nodes[id1]
    n2 = nodes[id2]
    node_dist_mat[id1][id2] = round(distanceInKmBetweenEarthCoordinates(n1.lat, n1.lon, n2.lat, n2.lon), 3)

In [18]:
node_dist_mat.shape

(196, 196)

In [19]:
node_dist_mat[:4, :4]

array([[  0.   ,  86.349,   0.   , 137.864],
       [ 86.349,   0.   ,   0.   , 146.07 ],
       [  0.   ,   0.   ,   0.   ,   0.   ],
       [137.864, 146.07 ,   0.   ,   0.   ]])

In [24]:
# depots are '040101', '130101', '150101'

depots = []
customers = []
for n in nodes:
    if n.is_depot:
        depots.append(n)
    else:
        customers.append(n)
depots_customers = depots + customers

with open('data/VRPTW_python/pedidosperu195.txt', 'w', newline='') as csvfile:
    spamwriter = csv.writer(csvfile, delimiter=' ', quoting=csv.QUOTE_MINIMAL)
    i = 0
    for node in depots_customers:
        spamwriter.writerow([
            #node.id,
            i,
            node.x, node.y,
            node.demand, node.ready_time, node.due_time, node.service_time
        ])
        i += 1

### Transformar a matriz conexa de nodos "customer"

In [ ]:
for n in nodes[:5]:
    print(n.__dict__)

In [ ]:
count = 0
for n in nodes:
    if n.demand:
        print(n.__dict__)
        count += 1
count

In [ ]:
#node_dist_mat = np.zeros((node_num, node_num))
elist = []

nodes_d = dict(zip([n.ubigeo for n in nodes], nodes))
for ubigeo1, ubigeo2 in tramos:
    #if ubigeo1 in nodes_d.keys() and ubigeo2 in nodes_d.keys():
    id1 = nodes_d[ubigeo1].id
    id2 = nodes_d[ubigeo2].id
    n1 = nodes[id1]
    n2 = nodes[id2]
    #node_dist_mat[id1][id2] = round(distanceInKmBetweenEarthCoordinates(n1.lat, n1.lon, n2.lat, n2.lon), 3)
    dist = round(distanceInKmBetweenEarthCoordinates(n1.lat, n1.lon, n2.lat, n2.lon), 3)
    elist.append((ubigeo1, ubigeo2, dist))
    
G = nx.Graph()
G.add_weighted_edges_from(elist)

In [ ]:
print(len(list(nodes_d)))
print(len(list(G.nodes)))

In [ ]:
G['010201']['010301']

In [ ]:
node_dist_mat[nodes_d['010201'].id, nodes_d['010301'].id]

In [ ]:
G['010201']['250301']

In [ ]:
path1 = nx.shortest_path(G, source='010201', target='250301', weight='weight')
path1

In [ ]:
path2 = nx.shortest_path(G, source='010201', target='250301')
path2

In [ ]:
l1, l2 = 0, 0
for i in range(len(path1)):
    if i == 0:
        continue
    l1 += G[path1[i-1]][path1[i]]['weight']
    l2 += G[path2[i-1]][path2[i]]['weight']
print(l1, l2)

In [ ]:
# https://stackoverflow.com/a/63169428/7498073
H = nx.subgraph(G, path1)
nx.draw(H, with_labels=True, font_weight='bold', node_color='lightblue', node_size=500)

In [ ]:
len_path = dict(nx.all_pairs_dijkstra(G, weight='weight'))
#for node, (dist, path) in len_path:
#    print(f"{node}: {dist} [{path}]")

In [ ]:
print(len_path['010201'][0]['250301'])
print(len_path['010201'][1]['250301'])

In [ ]:
help(G)

## Pruebitas